Loading the pre-trained model consumes too much time, we will simply recalculate it.

In [ ]:
!wget https://raw.githubusercontent.com/crow-intelligence/growth-hacking-sentiment/master/requirements.txt
!pip install -r requirements.txt

--2023-02-23 08:57:59--  https://raw.githubusercontent.com/crow-intelligence/growth-hacking-sentiment/master/requirements.txt
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 151 [text/plain]
Saving to: ‘requirements.txt’

requirements.txt    100%[===================>]     151  --.-KB/s    in 0s      

2023-02-23 08:57:59 (6.76 MB/s) - ‘requirements.txt’ saved [151/151]

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.5/250.5 KB 4.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 57.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 66.3 MB/s eta 0:00:00
     ━━━━━━━━━━━

In [ ]:
from google.colab import files

uploaded = files.upload()

Saving small_corpus.csv to small_corpus.csv


In [ ]:
import pandas as pd

df = pd.read_csv('small_corpus.csv')
df = df.dropna()
reviews = df['reviews'].dropna().values.tolist()

In [ ]:
def rating_2_sentiment_label(rating: int):
  if rating == 5:
    return 'positive'
  elif 2 <= rating <= 4:
    return 'neutral'
  elif rating == 1:
    return 'negative'

from sklearn.model_selection import train_test_split

# ground truth: y_true
df['sentiment_label'] = df['ratings'].apply(lambda x: rating_2_sentiment_label(x))
y_true = df['sentiment_label']

x_train, x_test, y_train, y_test = train_test_split(reviews, y_true,
                                                    test_size=0.20,
                                                    stratify=y_true)

# Preparing train data
train_df = pd.DataFrame({"text": x_train, "labels": y_train})
eval_df = pd.DataFrame({"text": x_test, "labels": y_test})

In [ ]:
from simpletransformers.classification import ClassificationModel, ClassificationArgs

In [ ]:
from sklearn.metrics import precision_score, recall_score, accuracy_score, precision_recall_fscore_support

In [ ]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Thu Feb 23 09:00:46 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 510.47.03    Driver Version: 510.47.03    CUDA Version: 11.6     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   67C    P0    26W /  70W |      0MiB / 15360MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
from psutil import virtual_memory
ram_gb = virtual_memory().total / 1e9
print('Your runtime has {:.1f} gigabytes of available RAM\n'.format(ram_gb))

if ram_gb < 20:
  print('Not using a high-RAM runtime')
else:
  print('You are using a high-RAM runtime!')

Your runtime has 13.6 gigabytes of available RAM

Not using a high-RAM runtime


In [ ]:
model_args = ClassificationArgs(labels_list=['positive', 'neutral', 'negative'], overwrite_output_dir=True, max_seq_length = 512, num_train_epochs = 1, evaluate_during_training = True, train_batch_size = 20, eval_batch_size = 20)  # num_train_epochs = 20, output_dir: ".\output_dir", best_model_dir = '.\best_model_dir\', 

model_distilbert_1_epoch_max_seq512 = ClassificationModel("distilbert", "distilbert-base-uncased", use_cuda = True, num_labels = 3, args = model_args)  # , model_name="distilbert")

model_distilbert_1_epoch_max_seq512.train_model(train_df, eval_df=eval_df, verbose=True)

predictions, raw_outputs = model_distilbert_1_epoch_max_seq512.predict(x_test)

print(accuracy_score(y_test, predictions))
print(precision_score(y_test, predictions, average=None))
print(recall_score(y_test, predictions, average=None))
precision_recall_fscore_support(y_test, predictions, average=None)

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.bias', 'vocab_transform.weight', 'vocab_projector.weight', 'vocab_projector.bias', 'vocab_layer_norm.weight', 'vocab_layer_norm.bias']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'classifier.bias', 'pre_classi

  0%|          | 0/4396 [00:00<?, ?it/s]

Now starts the real work

In [ ]:
from google.colab import files

uploaded = files.upload()

Saving big_corpus.csv to big_corpus.csv


In [ ]:
df_big = pd.read_csv("big_corpus.csv")
df_big = df_big.dropna()
reviews_big = df_big['reviews'].dropna().values.tolist()
# reviews_big

In [ ]:
def rating_2_sentiment_label(rating: int):
  if rating == 5:
    return 'positive'
  elif 2 <= rating <= 4:
    return 'neutral'
  elif rating == 1:
    return 'negative'

df_big['sentiment_label'] = df_big['ratings'].apply(lambda x: rating_2_sentiment_label(x))
y_true = df_big['sentiment_label']

In [ ]:
df_big

Unnamed: 0  ratings                                            reviews  \
0          366626      5.0  Love this game! So sad that they can't call it...   
1          150315      4.0  grandson played it a few times.  Seemed to lik...   
2           51294      5.0  What I liked the most is the freedom of moves....   
3          235082      4.0  First of all, i'm an avid fan of both franchis...   
4          298683      5.0  Amazing graphics and gameplay. I love the mech...   
...           ...      ...                                                ...   
99995       25722      5.0    I play this all the time!! Thank you so much !!   
99996       83896      1.0  I ordered the wrong game for wii I don't have ...   
99997      418450      5.0  Absolutely worth the money. Great product. Sol...   
99998      132443      5.0  I used this on the PSP 1000 and it worked perf...   
99999      201197      4.0  Its fun, even for adults. I bought this for my...   

      sentiment_label  
0            positive  
1             neutral  
2            positive  
3             neutral  
4            positive  
...               ...  
99995        positive  
99996        negative  
99997        positive  
99998        positive  
99999         neutral  

[99970 rows x 4 columns]

In [ ]:
y_true.shape

(99970,)

In [ ]:
# Let's make the prediction

In [ ]:
predictions, raw_outputs = model_distilbert_1_epoch_max_seq512.predict(reviews_big)

  0%|          | 0/99970 [00:00<?, ?it/s]

  0%|          | 0/4999 [00:00<?, ?it/s]

In [ ]:
# Let's create an histogram plot of the predicted labels distribution

In [ ]:
df_big["predictions"] = predictions

In [ ]:
df_big.to_csv("big_corpus_with_predictions.csv")

In [ ]:
files.download('big_corpus_with_predictions.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
df_big.groupby("predictions").agg("count").reset_index()

predictions  Unnamed: 0  ratings  reviews  sentiment_label  \
0    negative        6401     6401     6401             6401   
1     neutral       37276    37276    37276            37276   
2    positive       56293    56293    56293            56293   

   reviews_big_cleaned  
0                 6401  
1                37276  
2                56293

In [ ]:
import altair as alt
from vega_datasets import data

alt.Chart(df_big.groupby("predictions").agg("count").reset_index()).mark_bar().encode(
    alt.X("predictions", bin=False),
    y='reviews',
)

alt.Chart(...)

In [ ]:
# clean the data

In [ ]:
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
nltk.download('stopwords')
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [ ]:
reviews_big_cleaned = []

for review_big in reviews_big:
  sentences = sent_tokenize(review_big)
  filtered_sentences = []
  for sentence in sentences:
    words = word_tokenize(sentence)
    filtered_sentence = [w for w in words if not w.lower() in stop_words and w.isalpha()]
    filtered_sentences.append(filtered_sentence)

  reviews_big_cleaned.append(filtered_sentences)

In [ ]:
reviews_big_cleaned[:5]

[[['Love', 'game'],
  ['sad', 'ca', 'call', 'Harvest', 'Moon', 'Natsume', 'got', 'keep', 'name']],
 [['grandson', 'played', 'times'], ['Seemed', 'like']],
 [['liked', 'freedom', 'moves'],
  ['go', 'almost', 'everywhere'],
  ['sequel', 'Syberia'],
  ['decides',
   'time',
   'follow',
   'old',
   'man',
   'instead',
   'going',
   'like',
   'first',
   'one'],
  ['see', 'beautiful', 'scenario', 'amazing', 'puzzles'],
  ['love', 'end'],
  ['lot', 'see', 'wo', 'get', 'bored'],
  ['danger', 'easy', 'get', 'puzzles', 'traps', 'either'],
  ['really', 'enjoyed', 'basic', 'family', 'game'],
  ['Anybody', 'play'],
  ['way', 'maybe', 'need', 'patch', 'available', 'Internet'],
  ['got', 'first', 'one', 'game', 'would', 'play', 'nicely'],
  ['problem', 'second', 'one'],
  ['see', 'people', 'saying', 'game', 'working', 'well', 'PC'],
  ['think',
   'game',
   'playing',
   'funny',
   'seems',
   'defective',
   'try',
   'download',
   'patch',
   'maybe',
   'work',
   'second',
   'one']],
 [

In [ ]:
df_big['reviews_big_cleaned'] = reviews_big_cleaned

In [ ]:
from collections import Counter

def bigram_counts(sentences_list):
  ret = []
  for sentences in sentences_list:
    sentences_ret = []
    for word_list in sentences:
      bgs = list(nltk.bigrams(word_list))
      # print(bgs)

      sentences_ret.append(bgs)

    ret.append(sentences_ret)
	# fdist = nltk.FreqDist(bgs)
	# d = Counter()
	# for k, v in fdist.items():
	# 	d[k] = v
  # 
	# return d

  return ret

In [ ]:
reviews_big_cleaned[0]

[['Love', 'game'],
 ['sad', 'ca', 'call', 'Harvest', 'Moon', 'Natsume', 'got', 'keep', 'name']]

In [ ]:
# from scipy.sparse.linalg import bicgstab
# bgs = bigram_counts(reviews_big_cleaned)

In [ ]:
bigrams_corpus = []
for review_big_cleaned in reviews_big_cleaned:
  bigrams_sentences = []
  for sentence in review_big_cleaned:
    bigrams_sentences.append(nltk.bigrams(sentence))
  
  bigrams_corpus.append(bigrams_sentences)

[list(bc) for bc in bigrams_corpus[0]]

[[('Love', 'game')],
 [('sad', 'ca'),
  ('ca', 'call'),
  ('call', 'Harvest'),
  ('Harvest', 'Moon'),
  ('Moon', 'Natsume'),
  ('Natsume', 'got'),
  ('got', 'keep'),
  ('keep', 'name')]]

In [ ]:
# bigrams = nltk.bigrams(total_corpus_cleaned)
# list(bigrams)

In [ ]:
reviews_big[0]

"Love this game! So sad that they can't call it Harvest Moon but Natsume got to keep the name."

In [ ]:
def flatten3(l):
    return [i for sublist in l for item in sublist for i in item]

In [ ]:
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
nltk.download('stopwords')
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [ ]:
biagrms = df_big["bigrams"]
bigrams

0        [[('Love', 'game')], [('sad', 'ca'), ('ca', 'c...
1        [[('grandson', 'played'), ('played', 'times')]...
2        [[('liked', 'freedom'), ('freedom', 'moves')],...
3        [[('First', 'avid'), ('avid', 'fan'), ('fan', ...
4        [[('Amazing', 'graphics'), ('graphics', 'gamep...
                               ...                        
99965        [[('play', 'time')], [('Thank', 'much')], []]
99966    [[('ordered', 'wrong'), ('wrong', 'game'), ('g...
99967    [[('Absolutely', 'worth'), ('worth', 'money')]...
99968    [[('used', 'PSP'), ('PSP', 'worked'), ('worked...
99969    [[('fun', 'even'), ('even', 'adults')], [('bou...
Name: bigrams, Length: 99970, dtype: object

In [ ]:
bigrams_corpus = []
for sentence_bigrams in bigrams:
  bigrams_corpus.append(sentence_bigrams)

In [ ]:
bigram_corpus_one_line = flatten3(bigrams_corpus)

In [ ]:
frequency = nltk.FreqDist(bigram_corpus_one_line)

# for key, value in frequency.items():
#     print(list(key), value)

In [ ]:
# This is the most common bigrams in the whole corpus

frequency.most_common(150)

[(('game', 'play'), 4244),
 (('great', 'game'), 3790),
 (('play', 'game'), 3191),
 (('good', 'game'), 2823),
 (('playing', 'game'), 2650),
 (('fun', 'game'), 2622),
 (('feel', 'like'), 2556),
 (('video', 'game'), 2404),
 (('one', 'best'), 2302),
 (('single', 'player'), 2247),
 (('first', 'game'), 2160),
 (('like', 'game'), 2084),
 (('pretty', 'much'), 2045),
 (('much', 'better'), 1998),
 (('Final', 'Fantasy'), 1990),
 (('game', 'really'), 1964),
 (('games', 'like'), 1956),
 (('love', 'game'), 1939),
 (('game', 'great'), 1916),
 (('game', 'like'), 1815),
 (('pretty', 'good'), 1810),
 (('voice', 'acting'), 1767),
 (('game', 'fun'), 1764),
 (('lot', 'fun'), 1695),
 (('fun', 'play'), 1645),
 (('Great', 'game'), 1634),
 (('feels', 'like'), 1592),
 (('long', 'time'), 1586),
 (('game', 'ever'), 1586),
 (('video', 'games'), 1526),
 (('game', 'good'), 1499),
 (('would', 'recommend'), 1486),
 (('get', 'game'), 1473),
 (('highly', 'recommend'), 1460),
 (('much', 'fun'), 1453),
 (('even', 'though'

In [ ]:
df_big

Unnamed: 0  ratings                                            reviews  \
0          366626      5.0  Love this game! So sad that they can't call it...   
1          150315      4.0  grandson played it a few times.  Seemed to lik...   
2           51294      5.0  What I liked the most is the freedom of moves....   
3          235082      4.0  First of all, i'm an avid fan of both franchis...   
4          298683      5.0  Amazing graphics and gameplay. I love the mech...   
...           ...      ...                                                ...   
99995       25722      5.0    I play this all the time!! Thank you so much !!   
99996       83896      1.0  I ordered the wrong game for wii I don't have ...   
99997      418450      5.0  Absolutely worth the money. Great product. Sol...   
99998      132443      5.0  I used this on the PSP 1000 and it worked perf...   
99999      201197      4.0  Its fun, even for adults. I bought this for my...   

      sentiment_label predictions  \
0            positive    positive   
1             neutral    positive   
2            positive     neutral   
3             neutral     neutral   
4            positive    positive   
...               ...         ...   
99995        positive    positive   
99996        negative     neutral   
99997        positive    positive   
99998        positive    positive   
99999         neutral     neutral   

                                     reviews_big_cleaned  
0      [[Love, game], [sad, ca, call, Harvest, Moon, ...  
1            [[grandson, played, times], [Seemed, like]]  
2      [[liked, freedom, moves], [go, almost, everywh...  
3      [[First, avid, fan, franchises, cod, including...  
4      [[Amazing, graphics, gameplay], [love, mechani...  
...                                                  ...  
99995                  [[play, time], [Thank, much], []]  
99996  [[ordered, wrong, game, wii, wii, gave, friend...  
99997  [[Absolutely, worth, money], [Great, product],...  
99998  [[used, PSP, worked, perfectly], [make, sure, ...  
99999  [[fun, even, adults], [bought, old, daughter, ...  

[99970 rows x 6 columns]

In [ ]:
df_big.to_csv("df_big_with_predictions_and_tokenizations.csv")

In [ ]:
files.download("df_big_with_predictions_and_tokenizations.csv")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
# totals = [[], [], []]

# def sum_tokenized_sentences(sentiment_label, sentences):
#   global totals
#   if sentiment_label == "positive":
#     totals[0] += sentences
#   elif sentiment_label == "neutral":
#     totals[1] += sentences
#   if sentiment_label == "negetive":
#     totals[2] += sentences

#   return totals

# del sum

In [ ]:
df_big_agged_by_ground_truth = df_big.groupby("sentiment_label").agg({'reviews_big_cleaned': sum})
df_big_agged_by_ground_truth

reviews_big_cleaned
sentiment_label                                                   
negative         [[Great, game, hit, glitch, episode, EA, PUT, ...
neutral          [[grandson, played, times], [Seemed, like], [F...
positive         [[Love, game], [sad, ca, call, Harvest, Moon, ...

In [ ]:
df_big_agged_by_ground_truth[df_big_agged_by_ground_truth.index == "negative"]["reviews_big_cleaned"].iloc[0]

[['Great',
  'game',
  'hit',
  'glitch',
  'episode',
  'EA',
  'PUT',
  'GAMES',
  'glitches',
  'shame'],
 [],
 ['enough', 'missions'],
 [],
 ['Super', 'moves', 'work', 'boss', 'fights'],
 [],
 ['ca', 'turn', 'fight', 'time'],
 [],
 ['playable', 'sixth', 'rangers', 'like', 'Tommy', 'Jason'],
 [],
 ['Like',
  'Power',
  'Rangers',
  'Samurai',
  'Megazord',
  'battles',
  'stink',
  'even',
  'worse',
  'game'],
 [],
 ['never', 'get', 'perfect', 'score', 'unlock'],
 ['Orange', 'Ranger'],
 [],
 ['Even', 'two', 'year', 'old', 'beat', 'game'],
 [],
 ['Serpenterra', 'looks', 'horrible'],
 [],
 ['rangers', 'ranger', 'teams', 'game'],
 [],
 ['storyline',
  'terrible',
  'yet',
  'still',
  'annoying',
  'Power',
  'Rangers',
  'Megaforce',
  'game',
  'Nintendo'],
 ['Camera', 'sucks'],
 ['movements',
  'inhuman',
  'even',
  'cyborg',
  'biomechanics',
  'make',
  'sense',
  'first',
  'person'],
 ['FPS', 'bothered', 'eyes', 'much'],
 ['like', 'bad', 'ride', 'universal', 'studios'],
 ['sto

In [ ]:
# def tokenize_and_clean(total_reviews):
#   total_reviews_cleaned = []

#   # for review_big in reviews_big:
#   sentences = sent_tokenize(total_reviews)
#   filtered_sentences = []
#   for sentence in sentences:
#     words = word_tokenize(sentence)
#     filtered_sentence = [w for w in words if not w.lower() in stop_words and w.isalpha()]
#     # filtered_sentences.append(filtered_sentence)
#     total_reviews_cleaned.append(filtered_sentence)

#   return total_reviews_cleaned

In [ ]:
# bgs = bigram_counts([[["Hello", "World"]]])
# bgs

In [ ]:
df_big_agged_by_ground_truth["reviews_big_cleaned"]

sentiment_label
negative    [[Great, game, hit, glitch, episode, EA, PUT, ...
neutral     [[grandson, played, times], [Seemed, like], [F...
positive    [[Love, game], [sad, ca, call, Harvest, Moon, ...
Name: reviews_big_cleaned, dtype: object

In [ ]:
df_big_agged_by_ground_truth["bigram reviews"] = df_big_agged_by_ground_truth["reviews_big_cleaned"].apply(lambda x: bigram_counts([x]))
df_big_agged_by_ground_truth["bigram reviews"]

sentiment_label
negative    [[[('Great', 'game'), ('game', 'hit'), ('hit',...
neutral     [[[('grandson', 'played'), ('played', 'times')...
positive    [[[('Love', 'game')], [('sad', 'ca'), ('ca', '...
Name: bigram reviews, dtype: object

In [ ]:
df_big_agged_by_ground_truth["frequency bigram"] = df_big_agged_by_ground_truth["bigram reviews"].apply(lambda x: nltk.FreqDist(flatten(x)))
df_big_agged_by_ground_truth["frequency bigram"]

sentiment_label
negative    {('Great', 'game'): 11, ('game', 'hit'): 8, ('...
neutral     {('grandson', 'played'): 3, ('played', 'times'...
positive    {('Love', 'game'): 255, ('sad', 'ca'): 1, ('ca...
Name: frequency bigram, dtype: object

In [ ]:
df_big_agged_by_ground_truth.to_csv('df_big_agged_by_ground_truth.csv')

In [ ]:
df_big_agged_by_ground_truth["top frequency bigram"] = df_big_agged_by_ground_truth["frequency bigram"].apply(lambda x: x.most_common(150))

In [ ]:
files.download("df_big_agged_by_ground_truth.csv")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
df_big_agged_by_ground_truth

reviews_big_cleaned  \
sentiment_label                                                      
negative         [[Great, game, hit, glitch, episode, EA, PUT, ...   
neutral          [[grandson, played, times], [Seemed, like], [F...   
positive         [[Love, game], [sad, ca, call, Harvest, Moon, ...   

                                                    bigram reviews  \
sentiment_label                                                      
negative         [[[('Great', 'game'), ('game', 'hit'), ('hit',...   
neutral          [[[('grandson', 'played'), ('played', 'times')...   
positive         [[[('Love', 'game')], [('sad', 'ca'), ('ca', '...   

                                                  frequency bigram  \
sentiment_label                                                      
negative         {('Great', 'game'): 11, ('game', 'hit'): 8, ('...   
neutral          {('grandson', 'played'): 3, ('played', 'times'...   
positive         {('Love', 'game'): 255, ('sad', 'ca'): 1, ('ca...   

                                              top frequency bigram  
sentiment_label                                                     
negative         [((play, game), 334), ((game, play), 262), ((w...  
neutral          [((game, play), 2060), ((good, game), 1603), (...  
positive         [((great, game), 2363), ((game, play), 2000), ...

In [ ]:
from keyness import log_likelihood

In [ ]:
bigram_corpus_one_line

[('wanted', 'make'),
 ('make', 'game'),
 ('game', 'big'),
 ('big', 'making'),
 ('making', 'story'),
 ('story', 'bigger'),
 ('bigger', 'putting'),
 ('putting', 'million'),
 ('million', 'boring'),
 ('boring', 'repetitive'),
 ('repetitive', 'side'),
 ('side', 'quests'),
 ('quests', 'requiring'),
 ('requiring', 'complete'),
 ('complete', 'boring'),
 ('boring', 'things'),
 ('things', 'could'),
 ('could', 'get'),
 ('get', 'interesting'),
 ('interesting', 'parts'),
 ('parts', 'matter'),
 ('also', 'impressed'),
 ('impressed', 'could'),
 ('could', 'clear'),
 ('clear', 'area'),
 ('area', 'enemies'),
 ('enemies', 'endlessly'),
 ('endlessly', 'respawn'),
 ('respawn', 'around'),
 ('also', 'HORRIBLY'),
 ('HORRIBLY', 'time'),
 ('time', 'consuming'),
 ('consuming', 'keep'),
 ('keep', 'party'),
 ('party', 'armored'),
 ('armored', 'equipped'),
 ('equipped', 'well'),
 ('menu', 'system'),
 ('system', 'tedious'),
 ('tedious', 'could'),
 ('could', 'possibly'),
 ('War', 'Room'),
 ('Room', 'guess'),
 ('guess'

In [ ]:
df_big_agged_by_ground_truth["bigram reviews"]

sentiment_label
negative    [[[('Great', 'game'), ('game', 'hit'), ('hit',...
neutral     [[[('grandson', 'played'), ('played', 'times')...
positive    [[[('Love', 'game')], [('sad', 'ca'), ('ca', '...
Name: bigram reviews, dtype: object

In [ ]:
def flatten2(l):
    return [item for sublist in l for item in sublist]

In [ ]:
d_log_likelihood = {}
for sentiment in ["positive", "neutral", "negative"]:
  sentiment_corpus = flatten2(df_big_agged_by_ground_truth["bigram reviews"])
  d_log_likelihood[sentiment] = log_likelihood(bigram_corpus_one_line, sentiment_corpus)

# d_log_likelihood

NameError: ignored

In [ ]:
sentiment_corpus

NameError: ignored

The colab was shut down, let's try to revive it using the csv we had saved

In [ ]:
import pandas as pd

In [ ]:
from google.colab import files

uploaded = files.upload()

Saving df_big_with_predictions_and_tokenizations.csv to df_big_with_predictions_and_tokenizations (1).csv


In [ ]:
df_big = pd.read_csv('df_big_with_predictions_and_tokenizations.csv')

In [ ]:
df_big_agged = df_big.groupby("sentiment_label").agg({'reviews_big_cleaned': sum})

In [ ]:
# df_big_agged = pd.read_csv('df_big_agged_by_ground_truth.csv')

In [ ]:
df_big

Unnamed: 0  Unnamed: 0.1  ratings  \
0               0        366626      5.0   
1               1        150315      4.0   
2               2         51294      5.0   
3               3        235082      4.0   
4               4        298683      5.0   
...           ...           ...      ...   
99965       99995         25722      5.0   
99966       99996         83896      1.0   
99967       99997        418450      5.0   
99968       99998        132443      5.0   
99969       99999        201197      4.0   

                                                 reviews sentiment_label  \
0      Love this game! So sad that they can't call it...        positive   
1      grandson played it a few times.  Seemed to lik...         neutral   
2      What I liked the most is the freedom of moves....        positive   
3      First of all, i'm an avid fan of both franchis...         neutral   
4      Amazing graphics and gameplay. I love the mech...        positive   
...                                                  ...             ...   
99965    I play this all the time!! Thank you so much !!        positive   
99966  I ordered the wrong game for wii I don't have ...        negative   
99967  Absolutely worth the money. Great product. Sol...        positive   
99968  I used this on the PSP 1000 and it worked perf...        positive   
99969  Its fun, even for adults. I bought this for my...         neutral   

      predictions                                reviews_big_cleaned  
0        positive  [['Love', 'game'], ['sad', 'ca', 'call', 'Harv...  
1        positive  [['grandson', 'played', 'times'], ['Seemed', '...  
2         neutral  [['liked', 'freedom', 'moves'], ['go', 'almost...  
3         neutral  [['First', 'avid', 'fan', 'franchises', 'cod',...  
4        positive  [['Amazing', 'graphics', 'gameplay'], ['love',...  
...           ...                                                ...  
99965    positive          [['play', 'time'], ['Thank', 'much'], []]  
99966     neutral  [['ordered', 'wrong', 'game', 'wii', 'wii', 'g...  
99967    positive  [['Absolutely', 'worth', 'money'], ['Great', '...  
99968    positive  [['used', 'PSP', 'worked', 'perfectly'], ['mak...  
99969     neutral  [['fun', 'even', 'adults'], ['bought', 'old', ...  

[99970 rows x 7 columns]

In [ ]:
df_big_agged

reviews_big_cleaned
sentiment_label                                                   
negative         [['Great', 'game', 'hit', 'glitch', 'episode',...
neutral          [['grandson', 'played', 'times'], ['Seemed', '...
positive         [['Love', 'game'], ['sad', 'ca', 'call', 'Harv...

In [ ]:
# df_big_agged["frequency bigram"]

In [ ]:
# Bad result cell should have been save differently

In [ ]:
def flatten(l):
    return [i for sublist in l for item in sublist for i in item]

In [ ]:
!pip install keyness

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
nltk.download('stopwords')
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [ ]:
from ast import literal_eval

reviews_big_cleaned = df_big['reviews_big_cleaned'].apply(literal_eval)
print(reviews_big_cleaned[0])
print(type(reviews_big_cleaned[0]))

[['Love', 'game'], ['sad', 'ca', 'call', 'Harvest', 'Moon', 'Natsume', 'got', 'keep', 'name']]
<class 'list'>


In [ ]:
# reviews_big_cleaned = df_big['reviews_big_cleaned'].values.tolist()

bigrams_corpus = []
for review_big_cleaned in reviews_big_cleaned:
  # review_big_cleaned = list(review_big_cleaned)
  # print(review_big_cleaned)
  # print(type(review_big_cleaned))
  # break
  bigrams_sentences = []
  for sentence in review_big_cleaned:
    # print(sentence)
    bigrams_sentences.append(list(nltk.bigrams(sentence)))
    # print([print(item) for item in bigrams_sentences[-1]])
    # break
  
  # bigrams_corpus.append(nltk.bigrams(review_big_cleaned))
  bigrams_corpus.append(bigrams_sentences)

In [ ]:
bigrams_corpus

In [ ]:
df_big["bigrams"] = bigrams_corpus

In [ ]:
df_big

Unnamed: 0  Unnamed: 0.1  ratings  \
0               0        366626      5.0   
1               1        150315      4.0   
2               2         51294      5.0   
3               3        235082      4.0   
4               4        298683      5.0   
...           ...           ...      ...   
99965       99995         25722      5.0   
99966       99996         83896      1.0   
99967       99997        418450      5.0   
99968       99998        132443      5.0   
99969       99999        201197      4.0   

                                                 reviews sentiment_label  \
0      Love this game! So sad that they can't call it...        positive   
1      grandson played it a few times.  Seemed to lik...         neutral   
2      What I liked the most is the freedom of moves....        positive   
3      First of all, i'm an avid fan of both franchis...         neutral   
4      Amazing graphics and gameplay. I love the mech...        positive   
...                                                  ...             ...   
99965    I play this all the time!! Thank you so much !!        positive   
99966  I ordered the wrong game for wii I don't have ...        negative   
99967  Absolutely worth the money. Great product. Sol...        positive   
99968  I used this on the PSP 1000 and it worked perf...        positive   
99969  Its fun, even for adults. I bought this for my...         neutral   

      predictions                                reviews_big_cleaned  \
0        positive  [['Love', 'game'], ['sad', 'ca', 'call', 'Harv...   
1        positive  [['grandson', 'played', 'times'], ['Seemed', '...   
2         neutral  [['liked', 'freedom', 'moves'], ['go', 'almost...   
3         neutral  [['First', 'avid', 'fan', 'franchises', 'cod',...   
4        positive  [['Amazing', 'graphics', 'gameplay'], ['love',...   
...           ...                                                ...   
99965    positive          [['play', 'time'], ['Thank', 'much'], []]   
99966     neutral  [['ordered', 'wrong', 'game', 'wii', 'wii', 'g...   
99967    positive  [['Absolutely', 'worth', 'money'], ['Great', '...   
99968    positive  [['used', 'PSP', 'worked', 'perfectly'], ['mak...   
99969     neutral  [['fun', 'even', 'adults'], ['bought', 'old', ...   

                                                 bigrams  
0      [[(Love, game)], [(sad, ca), (ca, call), (call...  
1      [[(grandson, played), (played, times)], [(Seem...  
2      [[(liked, freedom), (freedom, moves)], [(go, a...  
3      [[(First, avid), (avid, fan), (fan, franchises...  
4      [[(Amazing, graphics), (graphics, gameplay)], ...  
...                                                  ...  
99965              [[(play, time)], [(Thank, much)], []]  
99966  [[(ordered, wrong), (wrong, game), (game, wii)...  
99967  [[(Absolutely, worth), (worth, money)], [(Grea...  
99968  [[(used, PSP), (PSP, worked), (worked, perfect...  
99969  [[(fun, even), (even, adults)], [(bought, old)...  

[99970 rows x 8 columns]

In [ ]:
df_big.to_csv('df_big_with_predictions_and_tokenizations_and_bigrams.csv')

In [ ]:
files.download("df_big_with_predictions_and_tokenizations_and_bigrams.csv")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Start again from beginning after disconnect

In [ ]:
from google.colab import files

uploaded = files.upload()

Saving df_big_with_predictions_and_tokenizations_and_bigrams.csv to df_big_with_predictions_and_tokenizations_and_bigrams.csv


In [5]:
import pandas as pd

In [6]:
df_big = pd.read_csv("df_big_with_predictions_and_tokenizations_and_bigrams.csv")

In [ ]:
def flatten3(l):
    return [i for sublist in l for item in sublist for i in item]

In [10]:
from ast import literal_eval

df_big["bigrams"] = df_big["bigrams"].apply(literal_eval)

In [ ]:
bigrams = df_big["bigrams"]

In [ ]:
df_big.head()

Unnamed: 0  Unnamed: 0.1  Unnamed: 0.1.1  ratings  \
0           0             0          366626      5.0   
1           1             1          150315      4.0   
2           2             2           51294      5.0   
3           3             3          235082      4.0   
4           4             4          298683      5.0   

                                             reviews sentiment_label  \
0  Love this game! So sad that they can't call it...        positive   
1  grandson played it a few times.  Seemed to lik...         neutral   
2  What I liked the most is the freedom of moves....        positive   
3  First of all, i'm an avid fan of both franchis...         neutral   
4  Amazing graphics and gameplay. I love the mech...        positive   

  predictions                                reviews_big_cleaned  \
0    positive  [['Love', 'game'], ['sad', 'ca', 'call', 'Harv...   
1    positive  [['grandson', 'played', 'times'], ['Seemed', '...   
2     neutral  [['liked', 'freedom', 'moves'], ['go', 'almost...   
3     neutral  [['First', 'avid', 'fan', 'franchises', 'cod',...   
4    positive  [['Amazing', 'graphics', 'gameplay'], ['love',...   

                                             bigrams  
0  [[(Love, game)], [(sad, ca), (ca, call), (call...  
1  [[(grandson, played), (played, times)], [(Seem...  
2  [[(liked, freedom), (freedom, moves)], [(go, a...  
3  [[(First, avid), (avid, fan), (fan, franchises...  
4  [[(Amazing, graphics), (graphics, gameplay)], ...

In [ ]:
df_big["bigrams"]

0        [[(Love, game)], [(sad, ca), (ca, call), (call...
1        [[(grandson, played), (played, times)], [(Seem...
2        [[(liked, freedom), (freedom, moves)], [(go, a...
3        [[(First, avid), (avid, fan), (fan, franchises...
4        [[(Amazing, graphics), (graphics, gameplay)], ...
                               ...                        
99965                [[(play, time)], [(Thank, much)], []]
99966    [[(ordered, wrong), (wrong, game), (game, wii)...
99967    [[(Absolutely, worth), (worth, money)], [(Grea...
99968    [[(used, PSP), (PSP, worked), (worked, perfect...
99969    [[(fun, even), (even, adults)], [(bought, old)...
Name: bigrams, Length: 99970, dtype: object

In [11]:
df_big["reviews_big_cleaned"] = df_big["reviews_big_cleaned"].apply(literal_eval)

In [12]:
df_agged = df_big.groupby("sentiment_label").agg({'reviews_big_cleaned': 'sum', 'bigrams': "sum"})

In [ ]:
df_agged

reviews_big_cleaned  \
sentiment_label                                                      
negative         [[Great, game, hit, glitch, episode, EA, PUT, ...   
neutral          [[grandson, played, times], [Seemed, like], [F...   
positive         [[Love, game], [sad, ca, call, Harvest, Moon, ...   

                                                           bigrams  
sentiment_label                                                     
negative         [[(Great, game), (game, hit), (hit, glitch), (...  
neutral          [[(grandson, played), (played, times)], [(Seem...  
positive         [[(Love, game)], [(sad, ca), (ca, call), (call...

In [ ]:
df_agged.to_csv("df_agged_reviews_and_bigrams.csv")

In [ ]:
files.download("df_agged_reviews_and_bigrams.csv")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
df_agged.head()

reviews_big_cleaned  \
sentiment_label                                                      
negative         [[Great, game, hit, glitch, episode, EA, PUT, ...   
neutral          [[grandson, played, times], [Seemed, like], [F...   
positive         [[Love, game], [sad, ca, call, Harvest, Moon, ...   

                                                           bigrams  
sentiment_label                                                     
negative         [[(Great, game), (game, hit), (hit, glitch), (...  
neutral          [[(grandson, played), (played, times)], [(Seem...  
positive         [[(Love, game)], [(sad, ca), (ca, call), (call...

In [ ]:
!pip install keyness

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Preparing metadata (setup.py) ... done
  Created wheel for keyness: filename=Keyness-0.25-py3-none-any.whl size=2572 sha256=49aa92fbe6966abb453fa3d7dff02cdfba8f8f01e13c21c7164741bb21caa4e9
  Stored in directory: /root/.cache/pip/wheels/f9/7c/28/68c81d914dc97d8753e1a90c5d64d86b07ad76a48b92bb8eb4
Successfully built keyness


In [ ]:
def flatten2(l):
    return [item for sublist in l for item in sublist]

In [ ]:
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
nltk.download('stopwords')
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [ ]:
bigrams = df_big["bigrams"]

bigrams_corpus = []
for bigram in bigrams:
  # bigrams_sentences = []
  # for sentence in bigrams:
  #   bigrams_sentences.append(list(nltk.bigrams(sentence)))
  
  bigrams_corpus.append(bigram)

In [ ]:
bigrams_corpus

[[[('Love', 'game')],
  [('sad', 'ca'),
   ('ca', 'call'),
   ('call', 'Harvest'),
   ('Harvest', 'Moon'),
   ('Moon', 'Natsume'),
   ('Natsume', 'got'),
   ('got', 'keep'),
   ('keep', 'name')]],
 [[('grandson', 'played'), ('played', 'times')], [('Seemed', 'like')]],
 [[('liked', 'freedom'), ('freedom', 'moves')],
  [('go', 'almost'), ('almost', 'everywhere')],
  [('sequel', 'Syberia')],
  [('decides', 'time'),
   ('time', 'follow'),
   ('follow', 'old'),
   ('old', 'man'),
   ('man', 'instead'),
   ('instead', 'going'),
   ('going', 'like'),
   ('like', 'first'),
   ('first', 'one')],
  [('see', 'beautiful'),
   ('beautiful', 'scenario'),
   ('scenario', 'amazing'),
   ('amazing', 'puzzles')],
  [('love', 'end')],
  [('lot', 'see'), ('see', 'wo'), ('wo', 'get'), ('get', 'bored')],
  [('danger', 'easy'),
   ('easy', 'get'),
   ('get', 'puzzles'),
   ('puzzles', 'traps'),
   ('traps', 'either')],
  [('really', 'enjoyed'),
   ('enjoyed', 'basic'),
   ('basic', 'family'),
   ('family', '

In [ ]:
bigram_corpus_one_line = flatten3(bigrams_corpus)

In [ ]:
for sentiment in ["negative", "neutral", "positive"]:
  print(df_agged[df_agged.index == sentiment])

                                               reviews_big_cleaned  \
sentiment_label                                                      
negative         [[Great, game, hit, glitch, episode, EA, PUT, ...   

                                                           bigrams  
sentiment_label                                                     
negative         [[(Great, game), (game, hit), (hit, glitch), (...  
                                               reviews_big_cleaned  \
sentiment_label                                                      
neutral          [[grandson, played, times], [Seemed, like], [F...   

                                                           bigrams  
sentiment_label                                                     
neutral          [[(grandson, played), (played, times)], [(Seem...  
                                               reviews_big_cleaned  \
sentiment_label                                                      
positive         [[Love,

In [ ]:
from keyness import log_likelihood

sentiment_2_bigrams = {}
d_log_likelihood = {}
for sentiment in ["negative", "neutral", "positive"]:
  sentiment_2_bigrams[sentiment] = flatten2(df_agged[df_agged.index == sentiment]["bigrams"])
  d_log_likelihood[sentiment] = log_likelihood(bigram_corpus_one_line, sentiment_2_bigrams[sentiment])
  # print(sentiment_2_bigrams[sentiment])
  # print(25 * "***")

In [ ]:
d_log_likelihood["positive"][:10]

[('game', 132701.459, 333558, 0),
 ('like', 40142.472, 100902, 0),
 ('games', 33374.084, 83889, 0),
 ('one', 31595.756, 79419, 0),
 ('get', 30315.519, 76201, 0),
 ('play', 27755.045, 69765, 0),
 ('good', 22957.538, 57706, 0),
 ('really', 21661.387, 54448, 0),
 ('great', 21049.117, 52909, 0),
 ('time', 20843.834, 52393, 0)]

In [ ]:
d_log_likelihood["negative"][:10]

[('game', 20285.434, 333558, 0),
 ('like', 6136.387, 100902, 0),
 ('games', 5101.736, 83889, 0),
 ('one', 4829.891, 79419, 0),
 ('get', 4634.188, 76201, 0),
 ('play', 4242.78, 69765, 0),
 ('good', 3509.408, 57706, 0),
 ('really', 3311.272, 54448, 0),
 ('great', 3217.677, 52909, 0),
 ('time', 3186.297, 52393, 0)]

In [ ]:
d_log_likelihood["positive"][0][0]

'game'

In [ ]:
type(d_log_likelihood["positive"][0][0])

str

In [ ]:
sentiment_to_keyness_bigrams = {}
for sentiment in ["negative", "neutral", "positive"]:
  keyness_bigrams = []
  total = 0
  for val in d_log_likelihood[sentiment]:
    if type(val[0]) == tuple:
      keyness_bigrams.append(val)
      total += 1
    if total >= 150:
      break

  sentiment_to_keyness_bigrams[sentiment] = keyness_bigrams

In [ ]:
sentiment_to_keyness_bigrams

{'negative': [(('play', 'game'), 2343.495, 0, 334),
  (('game', 'play'), 1838.311, 0, 262),
  (('waste', 'money'), 1536.603, 0, 219),
  (('buy', 'game'), 1529.587, 0, 218),
  (('playing', 'game'), 1122.632, 0, 160),
  (('single', 'player'), 1087.55, 0, 155),
  (('like', 'game'), 1059.484, 0, 151),
  (('game', 'ever'), 1045.451, 0, 149),
  (('pretty', 'much'), 1031.418, 0, 147),
  (('much', 'better'), 1010.369, 0, 144),
  (('bought', 'game'), 1003.353, 0, 143),
  (('video', 'game'), 989.32, 0, 141),
  (('feels', 'like'), 933.188, 0, 133),
  (('want', 'play'), 919.155, 0, 131),
  (('waste', 'time'), 905.122, 0, 129),
  (('good', 'game'), 877.057, 0, 125),
  (('game', 'would'), 877.057, 0, 125),
  (('feel', 'like'), 863.024, 0, 123),
  (('get', 'game'), 820.925, 0, 117),
  (('game', 'like'), 820.925, 0, 117),
  (('even', 'though'), 806.892, 0, 115),
  (('could', 'get'), 771.81, 0, 110),
  (('looks', 'like'), 771.81, 0, 110),
  (('game', 'even'), 757.777, 0, 108),
  (('ever', 'played'), 72

In [ ]:
print(df_big[df_big["sentiment_label"] == "negative"])

       Unnamed: 0  Unnamed: 0.1  Unnamed: 0.1.1  ratings  \
12             12            12          491259      1.0   
22             22            22          468660      1.0   
37             37            37          395292      1.0   
98             98            98          316467      1.0   
105           105           105          391586      1.0   
...           ...           ...             ...      ...   
99901       99901         99931          305704      1.0   
99913       99913         99943           85756      1.0   
99960       99960         99990          348317      1.0   
99963       99963         99993          211197      1.0   
99966       99966         99996           83896      1.0   

                                                 reviews sentiment_label  \
12     Great game until you hit the glitch in episode...        negative   
22     1.) Not enough missions . 2.) Super moves don'...        negative   
37     #1) The Camera sucks! The movements are inhu

In [ ]:
# you can see great game, and it looks like two words (bigram) is not enough to capture the context sometimes, since you need more context: "Great game until"

In [ ]:
# build data frame

lst_data = []

for sentiment, values in sentiment_to_keyness_bigrams.items():
  for value in values:
    lst_data.append([sentiment, value[0], value[1], value[2], value[3]])

df_results_bigrams = pd.DataFrame(lst_data, columns=["sentiment_label", "bigram", "log likelihood", "reference frequency", "corpus frequency"])

In [ ]:
df_results_bigrams

sentiment_label             bigram  log likelihood  reference frequency  \
0          negative       (play, game)        2343.495                    0   
1          negative       (game, play)        1838.311                    0   
2          negative     (waste, money)        1536.603                    0   
3          negative        (buy, game)        1529.587                    0   
4          negative    (playing, game)        1122.632                    0   
..              ...                ...             ...                  ...   
445        positive        (one, game)        1048.156                    0   
446        positive  (many, different)        1044.730                    0   
447        positive      (game, looks)        1041.305                    0   
448        positive   (favorite, game)        1034.454                    0   
449        positive       (look, like)        1034.454                    0   

     corpus frequency  
0                 334  
1                 262  
2                 219  
3                 218  
4                 160  
..                ...  
445               306  
446               305  
447               304  
448               302  
449               302  

[450 rows x 5 columns]

In [ ]:
df_results_bigrams.to_csv("df_results_bigrams.csv")

In [ ]:
files.download("df_results_bigrams.csv")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
# Notice refernce frequency is always 0! I don't know why... it seems like a bug in the package, maybe for tuples

In [ ]:
# There is no point to draw a graph of keyness against reference frequency

In [ ]:
### 
# Open the table of the positive bigrams and study the first 150 key phrases. Collect bigrams that express what customers like about video games. Mark the phrases with different colors to indicate that they express the following features. Customers:

# Like the game in general
# Like specific features of the game (e.g., graphics)
# Like the price of the game
# Recommend the game
### 

# Done and saved as "positive_features.xslx"

In [ ]:
# Open the table of the negative bigrams and study the first 150 key phrases. Collect bigrams that express what customers dislike about video games. Mark the phrases with different colors to indicate that they express the following features. Customers:
# Dislike the game in general
# Disike specific features of the game (e.g. voice)
# Save the document as negative_features.

# Done and saved under "negative_features.xslx"

In [ ]:
df_results_bigrams[df_results_bigrams["sentiment_label"] == "positive"]

sentiment_label             bigram  log likelihood  reference frequency  \
300        positive      (great, game)        8094.092                    0   
301        positive       (game, play)        6850.692                    0   
302        positive        (one, best)        5895.020                    0   
303        positive       (play, game)        5127.743                    0   
304        positive       (love, game)        4994.154                    0   
..              ...                ...             ...                  ...   
445        positive        (one, game)        1048.156                    0   
446        positive  (many, different)        1044.730                    0   
447        positive      (game, looks)        1041.305                    0   
448        positive   (favorite, game)        1034.454                    0   
449        positive       (look, like)        1034.454                    0   

     corpus frequency  
300              2363  
301              2000  
302              1721  
303              1497  
304              1458  
..                ...  
445               306  
446               305  
447               304  
448               302  
449               302  

[150 rows x 5 columns]

In [ ]:
# The list of negative key phrases also contains positive phrases (e.g., great game), because negation was disregarded when stop words were eliminated. Take a look at the positive words in the list of negative features (e.g., “great”) and check the context of the words. In this way you can make sure that you generated a correct list of key phrases with negative sentiment value; it is a natural phenomenon that a single phrase can be used both in negative and in positive context. Check the concordance of the words in the following steps:
# Sort the reviews into sentiment categories (positive, negative, and neutral).
# Convert them into nltk.Text. Don’t forget to apply nltk.word_tokenize.
# Print the concordance of “suspicious” positive words (e.g., great, fun) by calling the concordance method on the nltk.Text object that you created in the previous step.

In [7]:
df_big

Unnamed: 0  Unnamed: 0.1  Unnamed: 0.1.1  ratings  \
0               0             0          366626      5.0   
1               1             1          150315      4.0   
2               2             2           51294      5.0   
3               3             3          235082      4.0   
4               4             4          298683      5.0   
...           ...           ...             ...      ...   
99965       99965         99995           25722      5.0   
99966       99966         99996           83896      1.0   
99967       99967         99997          418450      5.0   
99968       99968         99998          132443      5.0   
99969       99969         99999          201197      4.0   

                                                 reviews sentiment_label  \
0      Love this game! So sad that they can't call it...        positive   
1      grandson played it a few times.  Seemed to lik...         neutral   
2      What I liked the most is the freedom of moves....        positive   
3      First of all, i'm an avid fan of both franchis...         neutral   
4      Amazing graphics and gameplay. I love the mech...        positive   
...                                                  ...             ...   
99965    I play this all the time!! Thank you so much !!        positive   
99966  I ordered the wrong game for wii I don't have ...        negative   
99967  Absolutely worth the money. Great product. Sol...        positive   
99968  I used this on the PSP 1000 and it worked perf...        positive   
99969  Its fun, even for adults. I bought this for my...         neutral   

      predictions                                reviews_big_cleaned  \
0        positive  [['Love', 'game'], ['sad', 'ca', 'call', 'Harv...   
1        positive  [['grandson', 'played', 'times'], ['Seemed', '...   
2         neutral  [['liked', 'freedom', 'moves'], ['go', 'almost...   
3         neutral  [['First', 'avid', 'fan', 'franchises', 'cod',...   
4        positive  [['Amazing', 'graphics', 'gameplay'], ['love',...   
...           ...                                                ...   
99965    positive          [['play', 'time'], ['Thank', 'much'], []]   
99966     neutral  [['ordered', 'wrong', 'game', 'wii', 'wii', 'g...   
99967    positive  [['Absolutely', 'worth', 'money'], ['Great', '...   
99968    positive  [['used', 'PSP', 'worked', 'perfectly'], ['mak...   
99969     neutral  [['fun', 'even', 'adults'], ['bought', 'old', ...   

                                                 bigrams  
0      [[('Love', 'game')], [('sad', 'ca'), ('ca', 'c...  
1      [[('grandson', 'played'), ('played', 'times')]...  
2      [[('liked', 'freedom'), ('freedom', 'moves')],...  
3      [[('First', 'avid'), ('avid', 'fan'), ('fan', ...  
4      [[('Amazing', 'graphics'), ('graphics', 'gamep...  
...                                                  ...  
99965      [[('play', 'time')], [('Thank', 'much')], []]  
99966  [[('ordered', 'wrong'), ('wrong', 'game'), ('g...  
99967  [[('Absolutely', 'worth'), ('worth', 'money')]...  
99968  [[('used', 'PSP'), ('PSP', 'worked'), ('worked...  
99969  [[('fun', 'even'), ('even', 'adults')], [('bou...  

[99970 rows x 9 columns]

In [30]:
import nltk
nltk.__version__

'3.7'

In [32]:
# from nltk import corpus  
# from nltk.text import Text  
# for negative_review in df_agged[df_agged.index == "negative"]["reviews_big_cleaned"]:
#   text = Text(negative_review)
#   text.concordance("great")
#   # print(output)

AttributeError: ignored

In [33]:
df_agged = df_big.groupby("sentiment_label").agg({'reviews': 'sum', 'reviews_big_cleaned': 'sum', 'bigrams': "sum"})

In [44]:
negative_corpus = df_agged[df_agged.index == "negative"]["reviews"]
negative_corpus = negative_corpus.iloc[0]

In [45]:
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
nltk.download('stopwords')
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [50]:
negative_corpus = negative_corpus.lower()

'great game until you hit the glitch in episode 8, why does ea put out games that have glitches shame on you!1.) not enough missions . 2.) super moves don\'t work in boss fights . 3.) you can\'t turn and fight at the same time . 4.) no playable sixth rangers like tommy or jason . 5.) like in power rangers samurai , the megazord battles stink ,but are even worse in this game . 6.) you can never get a perfect score and unlock the s.p.d. orange ranger . 7.) even a two year old can beat this game . 8.) serpenterra looks horrible . 9.) not all the rangers and ranger teams are in the game . 10.) the storyline is terrible ; and yet , still not as annoying as power rangers megaforce the game for nintendo 3ds .#1) the camera sucks! the movements are inhuman, even for a cyborg the biomechanics make no sense in the first person. no fps has bothered my eyes so much!! this is like a bad ride at universal studios!\n\n#2) the story is lack luster!!! weaker than cod ghost concerning story line and ant

In [63]:
# reviews_negative_cleaned = []

# # for review_big in reviews_big:
# negative_sentences = sent_tokenize(negative_corpus.lower())
# negative_filtered_sentences = []
# for negative_sentence in negative_sentences:
#   words = word_tokenize(negative_sentence)
#   negative_filtered_sentence = [w for w in words if not w.lower() in stop_words and w.isalpha()]
#   negative_filtered_sentences.append(negative_filtered_sentence)

In [70]:
# for review_big in reviews_big:
negative_tokens = word_tokenize(negative_corpus.lower())

In [71]:
negative_tokens

['great',
 'game',
 'until',
 'you',
 'hit',
 'the',
 'glitch',
 'in',
 'episode',
 '8',
 ',',
 'why',
 'does',
 'ea',
 'put',
 'out',
 'games',
 'that',
 'have',
 'glitches',
 'shame',
 'on',
 'you',
 '!',
 '1',
 '.',
 ')',
 'not',
 'enough',
 'missions',
 '.',
 '2',
 '.',
 ')',
 'super',
 'moves',
 'do',
 "n't",
 'work',
 'in',
 'boss',
 'fights',
 '.',
 '3',
 '.',
 ')',
 'you',
 'ca',
 "n't",
 'turn',
 'and',
 'fight',
 'at',
 'the',
 'same',
 'time',
 '.',
 '4',
 '.',
 ')',
 'no',
 'playable',
 'sixth',
 'rangers',
 'like',
 'tommy',
 'or',
 'jason',
 '.',
 '5',
 '.',
 ')',
 'like',
 'in',
 'power',
 'rangers',
 'samurai',
 ',',
 'the',
 'megazord',
 'battles',
 'stink',
 ',',
 'but',
 'are',
 'even',
 'worse',
 'in',
 'this',
 'game',
 '.',
 '6',
 '.',
 ')',
 'you',
 'can',
 'never',
 'get',
 'a',
 'perfect',
 'score',
 'and',
 'unlock',
 'the',
 's.p.d',
 '.',
 'orange',
 'ranger',
 '.',
 '7',
 '.',
 ')',
 'even',
 'a',
 'two',
 'year',
 'old',
 'can',
 'beat',
 'this',
 'game',


In [72]:
text = Text(negative_tokens)

In [76]:
lst_good_bigrams_in_negative_sentiment = [("great", "game"), ('want', 'play'), ('good', 'game'), ('fun', 'game')]

In [77]:
for good_bigram_in_negative_sentiment in lst_good_bigrams_in_negative_sentiment:
  print(good_bigram_in_negative_sentiment)
  print(text.concordance(list(good_bigram_in_negative_sentiment)))
  print(25 * "***")

('great', 'game')
Displaying 25 of 77 matches:
 great game until you hit the glitch in episo
llions developing what could be a great game only to kill it in the end with f
erning gamers or creating a truly great game . for many of us the poor control
er the consumer by re-releasing a great game in 2016 and pretending like it 's
rap with glitter if top . it is a great game for those who lack substance , st
ooter . destiny would have been a great game as a solo or a online multiplayer
 border of being an exceptionally great game . and although i wish to go back 
so , bahamians can not enjoy this great game again . what is being achieved by
t 's the point ? it 's actually a great game .. however it 's a great $ 20 gam
the damn game pad . this can be a great game with a small update to the contro
r , this would have been a really great game , but with them , it 's basically
a very good early release event ! great game ! i ordered this game for my coll
 n't play this game at allit 's a grea

In [84]:
# print("want")
wants = text.concordance("want", lines=2000)
print(type(wants))
# print("***")
# print("play")
# play = print(text.concordance("play"))
# for want in wants:
#   if "play" in want:
#     print(want)

Displaying 1050 of 1050 matches:
ing for 30 sec the only key you will want to hit is the delete key to deinstal
 ! navigation and gme play makes you want to scream and in the end you just wa
nt to scream and in the end you just want to use the disc as a fisbee in the t
lly makes gaming impossible . if you want a mouse that works for more than a w
 in a retail store because i did n't want to wait on shipping . the install se
lures of this game will make you not want to play it . they took a relativly s
erent consoles but this game made me want to scream . i paid $ 80 for the limi
ion ) . my daughter kept saying `` i want to just swim around '' , but the int
nd this game to anyone that does not want to continually shell out cash for ad
 are good . selecting the spells you want to learn instead of random is great 
necessarily long animations . if you want to spend hours of wanting to throw y
issing a jump and game over . if you want to enjoy the playing experience inst
 has been kidnapped

TypeError: ignored

In [78]:
# seems that with the bigger concept that can't be catched by bigrams the total meaning of the sentence is negative

In [ ]:
# even that "want", "play" wasn't matched. It's only due to stop words that avoided it, such as in this sentence: "no one would want to play"

In [87]:
# A report on results

In [88]:
df_big

Unnamed: 0  Unnamed: 0.1  Unnamed: 0.1.1  ratings  \
0               0             0          366626      5.0   
1               1             1          150315      4.0   
2               2             2           51294      5.0   
3               3             3          235082      4.0   
4               4             4          298683      5.0   
...           ...           ...             ...      ...   
99965       99965         99995           25722      5.0   
99966       99966         99996           83896      1.0   
99967       99967         99997          418450      5.0   
99968       99968         99998          132443      5.0   
99969       99969         99999          201197      4.0   

                                                 reviews sentiment_label  \
0      Love this game! So sad that they can't call it...        positive   
1      grandson played it a few times.  Seemed to lik...         neutral   
2      What I liked the most is the freedom of moves....        positive   
3      First of all, i'm an avid fan of both franchis...         neutral   
4      Amazing graphics and gameplay. I love the mech...        positive   
...                                                  ...             ...   
99965    I play this all the time!! Thank you so much !!        positive   
99966  I ordered the wrong game for wii I don't have ...        negative   
99967  Absolutely worth the money. Great product. Sol...        positive   
99968  I used this on the PSP 1000 and it worked perf...        positive   
99969  Its fun, even for adults. I bought this for my...         neutral   

      predictions                                reviews_big_cleaned  \
0        positive  [[Love, game], [sad, ca, call, Harvest, Moon, ...   
1        positive        [[grandson, played, times], [Seemed, like]]   
2         neutral  [[liked, freedom, moves], [go, almost, everywh...   
3         neutral  [[First, avid, fan, franchises, cod, including...   
4        positive  [[Amazing, graphics, gameplay], [love, mechani...   
...           ...                                                ...   
99965    positive                  [[play, time], [Thank, much], []]   
99966     neutral  [[ordered, wrong, game, wii, wii, gave, friend...   
99967    positive  [[Absolutely, worth, money], [Great, product],...   
99968    positive  [[used, PSP, worked, perfectly], [make, sure, ...   
99969     neutral  [[fun, even, adults], [bought, old, daughter, ...   

                                                 bigrams  
0      [[(Love, game)], [(sad, ca), (ca, call), (call...  
1      [[(grandson, played), (played, times)], [(Seem...  
2      [[(liked, freedom), (freedom, moves)], [(go, a...  
3      [[(First, avid), (avid, fan), (fan, franchises...  
4      [[(Amazing, graphics), (graphics, gameplay)], ...  
...                                                  ...  
99965              [[(play, time)], [(Thank, much)], []]  
99966  [[(ordered, wrong), (wrong, game), (game, wii)...  
99967  [[(Absolutely, worth), (worth, money)], [(Grea...  
99968  [[(used, PSP), (PSP, worked), (worked, perfect...  
99969  [[(fun, even), (even, adults)], [(bought, old)...  

[99970 rows x 9 columns]

In [ ]:
# From previous notebook, result on small corpus validation: 

# 0.7018181818181818
# [0.66917293 0.69980507 0.73208723]
# [0.59333333 0.718      0.78333333]
# (array([0.66917293, 0.69980507, 0.73208723]),
#  array([0.59333333, 0.718     , 0.78333333]),
#  array([0.62897527, 0.70878578, 0.7568438 ]),
#  array([300, 500, 300]))

In [100]:
from sklearn.metrics import precision_score, recall_score, accuracy_score, precision_recall_fscore_support

y_true = df_big["sentiment_label"]
y_pred = df_big["predictions"].values.tolist()

print(accuracy_score(y_true, y_pred))
print(precision_score(y_true, y_pred, average=None))
print(recall_score(y_true, y_pred, average=None))
precision_recall_fscore_support(y_true, y_pred, average=None)

0.7189356807042112
[0.50257772 0.59657689 0.82456078]
[0.51071599 0.66105826 0.77321717]


(array([0.50257772, 0.59657689, 0.82456078]),
 array([0.51071599, 0.66105826, 0.77321717]),
 array([0.50661417, 0.62716453, 0.79806403]),
 array([ 6299, 33640, 60031]))

In [101]:
# We can see a drop down in precision and recall, however it still yields the best results known so far (especially on the third label - positive)